In [8]:
import nibabel as nib
import numpy as np
import surfdist
from surfdist import *

import matplotlib.pyplot as plt
import nilearn.plotting 
import hcp_utils as hcp
import subprocess as sp
from nilearn import signal
from sklearn.metrics import pairwise_distances
from brainspace.gradient import GradientMaps

In [9]:
subj=100206
anatdir=f'/well/margulies/users/mnk884/{subj}/{subj}/Structural/'
fdir=f'/well/margulies/users/mnk884/{subj}/{subj}/Rest'

In [10]:
lcort=slice(0,29696)
rcort=slice(29696, 59412)
cortAll=slice(0,59412)

In [11]:
##### resting state time series paths 
ses1LR=f'{fdir}/rfMRI_REST1_LR_Atlas_hp2000_clean.dtseries.nii'
ses2LR=f'{fdir}/rfMRI_REST2_LR_Atlas_hp2000_clean.dtseries.nii'
ses1RL=f'{fdir}/rfMRI_REST1_RL_Atlas_hp2000_clean.dtseries.nii'
ses2RL=f'{fdir}/rfMRI_REST2_RL_Atlas_hp2000_clean.dtseries.nii'
func_ses=[ses1LR,ses2RL,ses1RL,ses2LR]

In [12]:
#### left anatomical files
Lsrf32=f'{anatdir}/{subj}.L.midthickness.32k_fs_LR.surf.gii'
LsrfNative=f'{anatdir}/{subj}.L.midthickness.native.surf.gii'
Lsphere32=f'{anatdir}/{subj}.L.sphere.32k_fs_LR.surf.gii'
LsphereNat=f'{anatdir}/{subj}.L.sphere.reg.reg_LR.native.surf.gii'
Laparc=f'{anatdir}/{subj}.L.aparc.a2009s.32k_fs_LR.label.gii'

#### right anatomical files 
Rsrf32=f'{anatdir}/{subj}.R.midthickness.32k_fs_LR.surf.gii'
RsrfNative=f'{anatdir}/{subj}.R.midthickness.native.surf.gii'
Rsphere32=f'{anatdir}/{subj}.R.sphere.32k_fs_LR.surf.gii'
RsphereNat=f'{anatdir}/{subj}.R.sphere.reg.reg_LR.native.surf.gii'
Raparc=f'{anatdir}/{subj}.R.aparc.a2009s.32k_fs_LR.label.gii'

In [13]:
def save_gifti(data,out):
	"""Save gifti file providing a numpy array and an output file path"""
	gi = nib.gifti.GiftiImage()
	da = nib.gifti.GiftiDataArray(np.float32(data), intent=0)
	gi.add_gifti_data_array(da)
	nib.save(gi,f'{out}.func.gii')


def post_smooth(func):
	"""Zscore normalize, bandpass filter, and remove first 10 volumes"""
	cifti=nib.load(func)
	#### clean the time series 
	cln=signal.clean(cifti.get_fdata(),detrend=True,standardize='zscore',filter='butterworth',low_pass=0.08,high_pass=0.008)
	return cln[10:]

def wb_smoothCleanTs(func_dat,kernel,leftSrf,rightSrf):
	"""" Smoooth, Normalize and Bandpass Filter data """
	inter=func_dat.split('dtseries.nii')[0]+f'{kernel}mm.dtseries.nii' #### named inter because file will be deleted
	cmd=f'wb_command -cifti-smoothing {func_dat} {kernel} {kernel} COLUMN {inter} -left-surface {leftSrf} -right-surface {rightSrf}'
	sp.run(cmd,shell=True)
	clnTs=post_smooth(inter)
	sp.run(f'rm {inter}',shell=True) 
	return clnTs

def get_corticalVertices(data):
	""" Get indices of Cortex Data from cifti file """
	cifti=nib.load(data)
	structMap=cifti.header.get_index_map(1)
	brainModels=list(structMap.brain_models)
	LCrtBM=brainModels[0]
	Lcrt_vrts=np.array(LCrtBM.vertex_indices)
	LnumVerts=LCrtBM.surface_number_of_vertices
	
	RCrtBM=brainModels[1]
	Rcrt_vrts=np.array(RCrtBM.vertex_indices)
	RnumVerts=RCrtBM.surface_number_of_vertices
	
	return {'lIDX':Lcrt_vrts,'lnverts':LnumVerts,'rIDX':Rcrt_vrts,'rnverts':RnumVerts}

def concat_sessions(DataList):
	return np.vstack([DataList[0],DataList[1]]).T, np.vstack([DataList[2],DataList[3]]).T

def pick_cortex(data,label):
	##### standard slices for HCP data and the 32k surface the time series are mapped on to 
	lcort=slice(0,29696)
	rcort=slice(29696, 59412)
	cortAll=slice(0,59412)
	###### slice time series based on hemisphere choice
	if label=='left':
		print('Using Left Cortex Only')
		data=data[lcort]
	elif label=='right':
		print('Using Right Cortex Only')
		data=data[rcort]
	else:
		print('Using whole cortex')
		data=data[cortAll]
	return data
		
####### use only if running locally. 
def calcFC(data):
	return np.corrcoef(data)


def calcFC_chunks(data):
	bigdata=data
	bigdata -= np.mean(bigdata, axis=1)[:,None]
	bigdata /= np.sqrt(np.sum(bigdata*bigdata, axis=1))[:,None]
	SPLITROWS = 1000
	numrows = bigdata.shape[0]
	res = np.memmap(f'{odir}/tmp.dat', 'float64', mode='w+', shape=(numrows, numrows))
	
	for r in range(0, numrows, SPLITROWS):
		for c in range(0, numrows, SPLITROWS):
			r1 = r + SPLITROWS
			c1 = c + SPLITROWS
			chunk1 = bigdata[r:r1]
			chunk2 = bigdata[c:c1]
			res[r:r1, c:c1] = np.dot(chunk1, chunk2.T)
	return res

def threshMat(conn,lim):
	perc = np.array([np.percentile(x, lim) for x in conn])
	# Threshold each row of the matrix by setting values below X percentile to 0
	for i in range(conn.shape[0]):
		conn[i, conn[i,:] < perc[i]] = 0   
	return conn

def pcaGrad(data):
	pca = GradientMaps(n_components=1, random_state=0,approach='pca')
	pca.fit(data)
	return pca.gradients_[:].squeeze()


def DiffEmbed(data,ngrads):
	####input is threshold FC matrix
# 	aff = 1 - pairwise_distances(data, metric = 'cosine')
	dm = GradientMaps(n_components=ngrads, random_state=42,approach='dm',kernel='cosine')
	dm.fit(data)
	return dm.gradients_

In [14]:
func_ses411=[]
for data in range(len(func_ses)):
	#### start by getting the indices of cortical vertices
	func_ses411.append(get_corticalVertices(func_ses[data]))
	##### smooth and clean the funcitonal time series
kernel=5.0 #### smoothed time series kernel

pixdim[1,2,3] should be non-zero; setting 0 dims to 1
pixdim[1,2,3] should be non-zero; setting 0 dims to 1
pixdim[1,2,3] should be non-zero; setting 0 dims to 1
pixdim[1,2,3] should be non-zero; setting 0 dims to 1


In [15]:
for data in range(len(func_ses)):
	##### smooth and clean the funcitonal time series
	func_ses[data]=wb_smoothCleanTs(func_ses[data],kernel,Lsrf32,Rsrf32)

In [17]:
funcs=[]
for i in func_ses:
    #### extract cortical ROIs
    funcs.append(i.T[cortAll])

del func_ses
data=np.hstack(funcs)

In [18]:
del funcs

In [24]:
tst=np.zeros(32492)
tst[func_ses411[0]['lIDX']]=data.T[0][lcort]

In [25]:
nilearn.plotting.view_surf(Lsrf32,tst)

In [26]:
rmat=np.corrcoef(data)

/gpfs3/well/margulies/users/mnk884/python/pkReliability-skylake/lib/python3.9/site-packages/numpy/lib/function_base.py:2690: RuntimeWarning: invalid value encountered in sqrt
  stddev = sqrt(d.real)


In [33]:
tst=np.zeros(32492)
tst[func_ses411[0]['lIDX']]=rmat[29000][lcort]
nilearn.plotting.view_surf(Lsrf32,tst)

In [ ]:
grads=DiffEmbed(rmat,3)

In [ ]:
grads